In [1]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler,StandardScaler
from keras.callbacks import ModelCheckpoint
import tensorflow as tf

In [2]:
merged = pd.read_csv(r'../data/long_merge.csv')

In [10]:
zones = [69, 68,67, 66,65.64, 42,41,40,39,38,37,36]
rtus = [1]
cols = []

for zone in zones:
        for column in merged.columns:
            if f"zone_0{zone}" in column and 'co2' not in column and "hw_valve" not in column and "cooling_sp" not in column and "heating_sp" not in column:
                cols.append(column)

for zone in zones:
        for column in merged.columns:
              if f"zone_0{zone}" in column and "cooling_sp" in column or "heating_sp" in column:
                cols.append(column)
# for rtu in rtus:
#     for column in merged.columns:
#         if f"rtu_00{rtu}_fltrd_sa" in column:
#                 cols.append(column)
cols =['date'] + cols + ['air_temp_set_1',
 'air_temp_set_2',
 'dew_point_temperature_set_1d',
 'relative_humidity_set_1',
 'solar_radiation_set_1']
input_dataset = merged[cols]

MemoryError: Unable to allocate 8.15 GiB for an array with shape (528, 2072154) and data type float64

In [11]:
input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = input_dataset[ (input_dataset.date.dt.date >date(2019, 1, 1)) & (input_dataset.date.dt.date< date(2021, 1, 1))]

if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

C:\Users\arbal\AppData\Local\Temp\ipykernel_32464\216607548.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")


MemoryError: Unable to allocate 8.15 GiB for an array with shape (528, 2070713) and data type float64

In [7]:
df_filtered

date  zone_069_temp  zone_069_fan_spd  zone_068_temp  \
1440    2018-01-02 00:00:00           71.4              20.0           73.2   
1441    2018-01-02 00:01:00           71.4              20.0           73.2   
1442    2018-01-02 00:02:00           71.4              20.0           73.2   
1443    2018-01-02 00:03:00           71.4              20.0           73.2   
1444    2018-01-02 00:04:00           71.4              20.0           73.2   
...                     ...            ...               ...            ...   
2072148 2020-12-31 23:57:00           68.8              20.0           71.7   
2072149 2020-12-31 23:58:00           68.8              20.0           71.7   
2072150 2020-12-31 23:58:00           68.8              20.0           71.7   
2072151 2020-12-31 23:59:00           68.8              20.0           71.7   
2072152 2020-12-31 23:59:00           68.8              20.0           71.7   

         zone_068_fan_spd  zone_067_temp  zone_067_fan_spd  zone_066_temp  \
1440                 70.0           71.2              20.0           70.4   
1441                 70.0           71.2              20.0           70.4   
1442                 70.0           71.2              20.0           70.4   
1443                 70.0           71.2              20.0           70.4   
1444                 70.0           71.2              20.0           70.4   
...                   ...            ...               ...            ...   
2072148              20.0           70.4              20.0           68.6   
2072149              20.0           70.4              20.0           68.6   
2072150              20.0           70.4              20.0           68.6   
2072151              20.0           70.4              20.0           68.6   
2072152              20.0           70.4              20.0           68.6   

         zone_066_fan_spd  zone_042_temp  ...  zone_066_heating_sp  \
1440                 35.0           71.6  ...                  NaN   
1441                 35.0           71.6  ...                  NaN   
1442                 35.0           71.6  ...                  NaN   
1443                 35.0           71.6  ...                  NaN   
1444                 35.0           71.6  ...                  NaN   
...                   ...            ...  ...                  ...   
2072148              35.0           71.4  ...                 68.0   
2072149              35.0           71.4  ...                 68.0   
2072150              35.0           71.4  ...                 68.0   
2072151              35.0           71.4  ...                 68.0   
2072152              35.0           71.4  ...                 68.0   

         zone_067_heating_sp  zone_069_heating_sp  zone_070_heating_sp  \
1440                     NaN                  NaN                  NaN   
1441                     NaN                  NaN                  NaN   
1442                     NaN                  NaN                  NaN   
1443                     NaN                  NaN                  NaN   
1444                     NaN                  NaN                  NaN   
...                      ...                  ...                  ...   
2072148                 68.0                 68.0                 65.0   
2072149                 68.0                 68.0                 65.0   
2072150                 68.0                 68.0                 65.0   
2072151                 68.0                 68.0                 65.0   
2072152                 68.0                 68.0                 65.0   

         zone_071_heating_sp  air_temp_set_1  air_temp_set_2  \
1440                     NaN          15.280          15.100   
1441                     NaN          15.280          15.100   
1442                     NaN          15.280          15.100   
1443                     NaN          15.280          15.100   
1444                     NaN          15.280          15.100   
...                      ...       

In [8]:
testdataset_df = df_filtered[(df_filtered.date.dt.date >date(2019, 5, 1)) & (df_filtered.date.dt.date <date(2019,7, 1))]

# traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]

traindataset_df = df_filtered[(df_filtered.date.dt.date >date(2019, 3, 1)) & (df_filtered.date.dt.date <date(2019, 5, 1))]
testdataset = testdataset_df.drop(columns=["date"]).rolling(window = 5, step = 1, min_periods= 1).mean().values
traindataset = traindataset_df.drop(columns=["date"]).rolling(window = 5, step = 1, min_periods= 1).mean().values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

['zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp',
 'zone_070_heating_sp']

In [9]:
traindataset_df.columns

Index(['date', 'zone_069_temp', 'zone_069_fan_spd', 'zone_068_temp',
       'zone_068_fan_spd', 'zone_067_temp', 'zone_067_fan_spd',
       'zone_066_temp', 'zone_066_fan_spd', 'zone_042_temp',
       ...
       'zone_066_heating_sp', 'zone_067_heating_sp', 'zone_069_heating_sp',
       'zone_070_heating_sp', 'zone_071_heating_sp', 'air_temp_set_1',
       'air_temp_set_2', 'dew_point_temperature_set_1d',
       'relative_humidity_set_1', 'solar_radiation_set_1'],
      dtype='object', length=529)

In [123]:
print(traindataset_df.isna().sum().sum(), testdataset_df.isna().sum().sum())

0 0


In [124]:
len(traindataset), len(testdataset)

(86400, 86400)

In [125]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = StandardScaler()
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [126]:
traindataset.shape

(86400, 45)

In [127]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = []
    Y = []
    for i in range(len(dataset) - time_step - 1):
        x.append(dataset[i:(i+time_step),:])
        Y.append(dataset[i+time_step,0:-5])
    x= np.array(x)
    Y = np.array(Y)
    return x,Y
time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)



In [128]:
X_train.shape, y_train.shape

((86369, 30, 45), (86369, 40))

In [133]:

model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=y_train.shape[1]))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm_vav_01.tf"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=128, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5
674/675 [============================>.] - ETA: 0s - loss: 0.1090
Epoch 1: val_loss improved from inf to 0.26433, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


675/675 [==============================] - 61s 84ms/step - loss: 0.1089 - val_loss: 0.2643
Epoch 2/5
675/675 [==============================] - ETA: 0s - loss: 0.0155
Epoch 2: val_loss improved from 0.26433 to 0.21391, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


675/675 [==============================] - 45s 67ms/step - loss: 0.0155 - val_loss: 0.2139
Epoch 3/5
675/675 [==============================] - ETA: 0s - loss: 0.0081
Epoch 3: val_loss improved from 0.21391 to 0.17155, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


...

675/675 [==============================] - 58s 86ms/step - loss: 0.0081 - val_loss: 0.1716
Epoch 4/5
675/675 [==============================] - ETA: 0s - loss: 0.0049
Epoch 4: val_loss improved from 0.17155 to 0.14438, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


675/675 [==============================] - 54s 80ms/step - loss: 0.0049 - val_loss: 0.1444
Epoch 5/5
675/675 [==============================] - ETA: 0s - loss: 0.0030
Epoch 5: val_loss improved from 0.14438 to 0.12414, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


675/675 [==============================] - 60s 89ms/step - loss: 0.0030 - val_loss: 0.1241


In [134]:
model.load_weights(checkpoint_path)

In [135]:
test_predict1 = model.predict(X_test)

2700/2700 [==============================] - 25s 9ms/step


In [136]:
plt.plot(y_test[:,3])
plt.plot(y_train[:,3])

In [141]:
%matplotlib qt
var = 1
plt.plot(y_test[:,var], label='Original Testing Data', color='blue')
plt.plot(test_predict1[:,var], label='Predicted Testing Data', color='red',alpha=0.8)
anomalies = np.where(abs(test_predict1[:,var] - y_test[:,var]) > 0.38)
plt.scatter(anomalies,test_predict1[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [18]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X =  test_predict1 - y_test


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2)

# Fitting the model to the data
gmm.fit(X)

# Getting the cluster labels
labels = gmm.predict(X)

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [19]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
# Generating random data for demonstration
np.random.seed(0)
X = (test_predict1 - y_test)

k = 6

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


ValueError: operands could not be broadcast together with shapes (199403,51) (8,) 

In [ ]:
k = 60
X= test_predict1 - y_test
processed_data = []
feat_df = pd.DataFrame(columns=["mean","std",])
for i in range(0,len(X), 60):
    mean = X[i:i+k].mean(axis = 0)
    std = X[i:i+k].std(axis = 0)
    max = X[i:i+k].max(axis = 0)
    min = X[i:i+k].min(axis = 0)
    iqr = np.percentile(X[i:i+k], 75, axis=0) - np.percentile(X[i:i+k], 25,axis=0)
    data = np.concatenate([mean, std, max, min, iqr])
    processed_data.append([data])
processed_data = np.concatenate(processed_data,axis=0) 

In [ ]:
X = processed_data

kmeans = KMeans(n_clusters=3, algorithm='elkan', max_iter=1000, n_init = 5)

kmeans.fit(X)

pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [ ]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = processed_data

# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=3, init_params='k-means++')

# Fitting the model to the data
gmm.fit(X)
labels = gmm.predict(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster labels

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()



In [ ]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
# Generating random data for demonstration
np.random.seed(0)
X = (test_predict1 * scaler.var_[0:8] + scaler.mean_[0:8]) - (y_test * scaler.var_[0:8] + scaler.mean_[0:8])
k = 6

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()
